In [1]:
import pandas as pd

df = pd.read_parquet("./inputs")
df

name sex  \
0        Richard Clarke   M   
1        Lisa Carpenter   F   
2          Barbara Ruiz   F   
3       Leslie Mitchell   F   
4       Jason Patterson   M   
...                 ...  ..   
1995       Alexa Harris   F   
1996     Miguel Jackson   M   
1997     Amanda Griffin   F   
1998      Kyle Morrison   M   
1999  Sharon Cooper DVM   F   

                                                address  \
0               533 Sarah Summit\nCharlesport, TN 87961   
1                23539 Cox Viaduct\nLucasberg, NE 99946   
2                      Unit 0222 Box 4192\nDPO AA 61786   
3     7007 Rebecca Fall Apt. 131\nPort Michelleberg,...   
4                      PSC 8182, Box 0863\nAPO AE 04174   
...                                                 ...   
1995  136 Erica Station Suite 628\nGonzalesmouth, MN...   
1996           2111 Johnson Ferry\nStevenside, WY 78990   
1997  4273 Theresa Path Suite 332\nMalonechester, OK...   
1998            0511 Mcdonald Burg\nLanceberg, VA 41173   
1999      22218 Davis Harbors\nWilliamsonport, WA 86966   

                         email   birthdate          ssn  
0           iramirez@yahoo.com  1913-05-23  074-22-3263  
1          tyler70@hotmail.com  1917-11-01  887-66-2475  
2         pdavenport@gmail.com  1945-12-24  562-95-4601  
3             leah62@gmail.com  1914-01-23  831-70-3890  
4        adamsdarius@yahoo.com  1923-12-30  696-81-4835  
...                        ...         ...          ...  
1995       patrick73@yahoo.com  1992-05-23  735-99-2426  
1996       vancemary@yahoo.com  2000-08-31  555-99-0241  
1997  laurenmiller@hotmail.com  2011-11-24  377-74-5469  
1998       william30@yahoo.com  1966-07-28  406-66-6296  
1999    williamslisa@yahoo.com  1935-11-21  058-84-0396  

[2000 rows x 6 columns]

In [2]:
dude = df.iloc[0]
dude

name                                  Richard Clarke
sex                                                M
address      533 Sarah Summit\nCharlesport, TN 87961
email                             iramirez@yahoo.com
birthdate                                 1913-05-23
ssn                                      074-22-3263
Name: 0, dtype: object

In [30]:
from fhir.resources.patient import Patient
from fhir.resources import construct_fhir_element

json_obj = {
    "resourceType": "Patient",
    "name": [{"text": dude["name"]}],
    "gender": dude["sex"],  # TODO: map to male | female | other | unknown
    "address": [
        {
            "text": dude["address"],
        },
    ],
    "telecom": [
        {
            "system": "email",
            "value": dude["email"],
        },
    ],
    "birthDate": dude["birthdate"],
    "identifier": [
        {
            "type": {
                "coding": [
                    {
                        "system": "http://terminology.hl7.org/CodeSystem/v2-0203",
                        "code": "SS",
                    }
                ]
            },
            "system": "http://hl7.org/fhir/sid/us-ssn",
            "value": dude["ssn"],  # TODO: map to remove ^\d
        },
    ],
}
pat = Patient.parse_obj(json_obj)
# pat.name
# pat.birthDate
# pat.gender
# pat.address
# pat.telecom
# pat.identifier
pat

Patient(resource_type='Patient', fhir_comments=None, id=None, id__ext=None, implicitRules=None, implicitRules__ext=None, language=None, language__ext=None, meta=None, contained=None, extension=None, modifierExtension=None, text=None, active=None, active__ext=None, address=[Address(resource_type='Address', fhir_comments=None, extension=None, id=None, id__ext=None, city=None, city__ext=None, country=None, country__ext=None, district=None, district__ext=None, line=None, line__ext=None, period=None, postalCode=None, postalCode__ext=None, state=None, state__ext=None, text='533 Sarah Summit\nCharlesport, TN 87961', text__ext=None, type=None, type__ext=None, use=None, use__ext=None)], birthDate=datetime.date(1913, 5, 23), birthDate__ext=None, communication=None, contact=None, deceasedBoolean=None, deceasedBoolean__ext=None, deceasedDateTime=None, deceasedDateTime__ext=None, gender='M', gender__ext=None, generalPractitioner=None, identifier=[Identifier(resource_type='Identifier', fhir_comments

In [19]:
from fhir.resources import construct_fhir_element

# convert string address into FHIR address
address = "533 Sarah Summit\nCharlesport, TN 87961"
construct_fhir_element("Address", {"text": address})

Address(resource_type='Address', fhir_comments=None, extension=None, id=None, id__ext=None, city=None, city__ext=None, country=None, country__ext=None, district=None, district__ext=None, line=None, line__ext=None, period=None, postalCode=None, postalCode__ext=None, state=None, state__ext=None, text='533 Sarah Summit\nCharlesport, TN 87961', text__ext=None, type=None, type__ext=None, use=None, use__ext=None)

In [3]:
import os

destination = "./output"
if not os.path.isdir(destination):
    os.mkdir(destination)

In [60]:
json_template = """{
  "resourceType" : "Patient",
  "name" : [{ HumanName }], // A name associated with the patient

  "identifier" : [{ Identifier }], // An identifier for this patient
  "active" : <boolean>, // Whether this patient's record is in active use
  "telecom" : [{ ContactPoint }], // A contact detail for the individual
  "gender" : "<code>", // male | female | other | unknown
  "birthDate" : "<date>", // The date of birth for the individual
  "deceasedBoolean" : <boolean>,
  "deceasedDateTime" : "<dateTime>",
  "address" : [{ Address }], // An address for the individual
  "maritalStatus" : { CodeableConcept }, // Marital (civil) status of a patient
  "multipleBirthBoolean" : <boolean>,
  "multipleBirthInteger" : <integer>,
  "photo" : [{ Attachment }], // Image of the patient
  "contact" : [{ // A contact party (e.g. guardian, partner, friend) for the patient
    "relationship" : [{ CodeableConcept }], // The kind of relationship
    "name" : { HumanName }, // A name associated with the contact person
    "telecom" : [{ ContactPoint }], // A contact detail for the person
    "address" : { Address }, // Address for the contact person
    "gender" : "<code>", // male | female | other | unknown
    "organization" : { Reference(Organization) }, // C? Organization that is associated with the contact
    "period" : { Period } // The period during which this contact person or organization is valid to be contacted relating to this patient
  }],
  "communication" : [{ // A language which may be used to communicate with the patient about his or her health
    "language" : { CodeableConcept }, // R!  The language which can be used to communicate with the patient about his or her health
    "preferred" : <boolean> // Language preference indicator
  }],
  "generalPractitioner" : [{ Reference(Organization|Practitioner|
   PractitionerRole) }], // Patient's nominated primary care provider
  "managingOrganization" : { Reference(Organization) }, // Organization that is the custodian of the patient record
  "link" : [{ // Link to another patient resource that concerns the same actual person
    "other" : { Reference(Patient|RelatedPerson) }, // R!  The other patient or related person resource that the link refers to
    "type" : "<code>" // R!  replaced-by | replaces | refer | seealso
  }]
}"""

In [16]:
import json

from fhir.resources.patient import Patient
from fhir.resources.humanname import HumanName
from datetime import date


def get_birth_date(d):
    return "xxx"


def raw_to_patient_json(row):
    json_obj = {}
    pat = Patient.parse_obj(json_obj)
    print(pat)
    return json.dumps(
        {
            "resourceType": "Patient",
            "name": [
                row["name"],  # https://www.hl7.org/fhir/datatypes.html#HumanName
            ],
            "gender": row["sex"],  # enum - male | female | other | unknown
            "birthdate": get_birth_date(row["birthdate"]),
            "address": [
                row["address"],  # trans Address
            ],
            "telecom": [
                # 'email': 'xxx',
            ],
            "ssn": "sss",
        }
    )


row = df.iloc[0]
# row
raw_to_patient_json(row)

resource_type='Patient' fhir_comments=None id=None id__ext=None implicitRules=None implicitRules__ext=None language=None language__ext=None meta=None contained=None extension=None modifierExtension=None text=None active=None active__ext=None address=None birthDate=None birthDate__ext=None communication=None contact=None deceasedBoolean=None deceasedBoolean__ext=None deceasedDateTime=None deceasedDateTime__ext=None gender=None gender__ext=None generalPractitioner=None identifier=None link=None managingOrganization=None maritalStatus=None multipleBirthBoolean=None multipleBirthBoolean__ext=None multipleBirthInteger=None multipleBirthInteger__ext=None name=None photo=None telecom=None


'{"resourceType": "Patient", "name": ["Richard Clarke"], "gender": "M", "birthdate": "xxx", "address": ["533 Sarah Summit\\nCharlesport, TN 87961"], "telecom": [], "ssn": "sss"}'

In [52]:
import uuid
import json


def get_patient_meta(row):
    # print(row)
    patient_json = raw_to_patient_json(row)
    patient_uuid = str(uuid.uuid4())
    return (
        patient_uuid,
        patient_json,
    )


def write_file(destination, content):
    # TODO: consider overwrite
    f = open(filepath, "w")
    f.write(content)
    f.close()


for index, row in df.iterrows():
    patient_meta = get_patient_meta(row)
    print(patient_meta)
    filename = f"{patient_meta[0]}.json"
    filepath = os.path.join(destination, filename)
    print(filepath)
    patient = patient_meta[1]
    write_file(destination, json.dumps(patient))

('38697988-52fe-4ef1-9680-c35e1b71697d', '{\n  "resourceType" : "Patient",\n  // from Resource: id, meta, implicitRules, and language\n  // from DomainResource: text, contained, extension, and modifierExtension\n  "identifier" : [{ Identifier }], // An identifier for this patient\n  "active" : <boolean>, // Whether this patient\'s record is in active use\n  "name" : [{ HumanName }], // A name associated with the patient\n  "telecom" : [{ ContactPoint }], // A contact detail for the individual\n  "gender" : "<code>", // male | female | other | unknown\n  "birthDate" : "<date>", // The date of birth for the individual\n  // deceased[x]: Indicates if the individual is deceased or not. One of these 2:\n  "deceasedBoolean" : <boolean>,\n  "deceasedDateTime" : "<dateTime>",\n  "address" : [{ Address }], // An address for the individual\n  "maritalStatus" : { CodeableConcept }, // Marital (civil) status of a patient\n  // multipleBirth[x]: Whether patient is part of a multiple birth. One of t

In [1]:
row = df.iloc[0]
row
p = get_patient(row)
p

NameError: name 'df' is not defined